In [1]:
if 'dbutils' in locals():
    dbutils.library.restartPython()

!python --version

Python 3.11.9


In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
import os
import sys
from pathlib import Path

workding_dir = str(Path.cwd().parent)
os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: /home/inflaton/code/projects/courses/logical-reasoning


In [4]:
need_to_setup_env = False
need_to_setup_env

False

In [5]:
if need_to_setup_env:
    %pip config set global.index-url https://artifacts.forge.mastercard.com/artifactory/api/pypi/python/simple
    %pip install tf-keras
    %pip install -q --upgrade accelerate einops xformers torchvision
    %pip install -r requirements.txt
    !cd ../LLaMA-Factory && pip install -e .[torch,bitsandbytes] && FLASH_ATTENTION_FORCE_BUILD=TRUE pip install --upgrade flash-attn

In [6]:
os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: /home/inflaton/code/projects/courses/logical-reasoning


In [7]:
from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

loading env vars from: /home/inflaton/code/projects/courses/logical-reasoning/.env


True

In [8]:
import os

model_name = os.getenv("MODEL_NAME")
adapter_name_or_path = os.getenv("ADAPTER_NAME_OR_PATH")
load_in_4bit = os.getenv("LOAD_IN_4BIT") == "true"
data_path = os.getenv("LOGICAL_REASONING_DATA_PATH")
results_path = os.getenv("LOGICAL_REASONING_RESULTS_PATH")
use_english_datasets = os.getenv("USE_ENGLISH_DATASETS") == "true"

print(model_name, adapter_name_or_path, load_in_4bit, data_path, results_path)

internlm/internlm2_5-7b-chat-1m None True datasets/mgtv results/mgtv-results_nv4080_r2.csv


In [9]:
!nvidia-smi

Wed Jul 10 23:11:43 2024       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 545.23.07              Driver Version: 546.12       CUDA Version: 12.3     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  NVIDIA GeForce RTX 4080 ...    On  | 00000000:01:00.0 Off |                  N/A |
| N/A   49C    P0              28W / 150W |      0MiB / 12282MiB |      0%      Default |
|                                         |                      |                  N/A |
+-----------------------------------------+----------------------+--

In [10]:
%%time
!python --version
!pip show flash-attn

Python 3.11.9
CPU times: user 9.97 ms, sys: 1.61 ms, total: 11.6 ms
Wall time: 491 ms


In [11]:
def evaluate_model_all_epochs(model_name, adapter_path_base, num_train_epochs, start_epoch=0, load_in_4bit=True, num_of_entries=-1):
    os.environ["MODEL_NAME"] = model_name 
    os.environ["LOAD_IN_4BIT"] = "true" if load_in_4bit else "false"
    for i in range(start_epoch, num_train_epochs + 1):
        print(f"Epoch {i}")
        if i == 0:
            os.unsetenv("ADAPTER_NAME_OR_PATH")
        else:
            adapter_path = f"{adapter_path_base}/checkpoint-{562 * i}"
            os.environ["ADAPTER_NAME_OR_PATH"] = adapter_path
            
        !python llm_toolkit/eval_logical_reasoning.py {num_of_entries}

In [12]:
%%time

evaluate_model_all_epochs("internlm/internlm2_5-7b-chat-1m", "llama-factory/saves/internlm2_5_7b/lora/sft", 6, start_epoch=1, load_in_4bit=True, num_of_entries=-1)

Epoch 1
loading env vars from: /home/inflaton/code/projects/courses/logical-reasoning/.env
Adding /home/inflaton/code/projects/courses/logical-reasoning to sys.path
loading /home/inflaton/code/projects/courses/logical-reasoning/llm_toolkit/logical_reasoning_utils.py
internlm/internlm2_5-7b-chat-1m llama-factory/saves/internlm2_5_7b/lora/sft/checkpoint-562 True datasets/mgtv results/mgtv-results_nv4080_r2.csv
(1) GPU = NVIDIA GeForce RTX 4080 Laptop GPU. Max memory = 11.994 GB.
0.0 GB of memory reserved.
loading model: internlm/internlm2_5-7b-chat-1m
[INFO|tokenization_utils_base.py:2161] 2024-07-10 23:11:52,011 >> loading file ./tokenizer.model from cache at /home/inflaton/.cache/huggingface/hub/models--internlm--internlm2_5-7b-chat-1m/snapshots/8d1a709a04d71440ef3df6ebbe204672f411c8b6/./tokenizer.model
[INFO|tokenization_utils_base.py:2161] 2024-07-10 23:11:52,011 >> loading file added_tokens.json from cache at None
[INFO|tokenization_utils_base.py:2161] 2024-07-10 23:11:52,011 >> loa